# Lecture 12: Spark DataFrame transformations

## Learning objectives

By the end of this lecture, students should be able to carry out the following transformations in Spark DataFrames:
- Replacing null values;
- Removing duplicated values;
- Merging multiple DataFrames with UNION operations;
- Merging multiple DataFrames with JOIN operations;
- Rows to columns and columns to rows with Pivot operations;
- Collecting and explode operations


## Import sample data from MongoDB

To connect MongoDB cluster to databricks you need to:
1. Change Network Access IP on MongoDB cluster to `0.0.0.0/0`
  - Open MongoDB cluster
  - Navgivate to the Network Access tab on the left
  - Click `Add IP address`
  - Add the following IP `0.0.0.0/0`
2. Install the Spark MongoDB connector via Maven: `org.mongodb.spark:mongo-spark-connector_2.13:10.4.0`
  - Open databricks
  - Navigate to your workspace, click `Compute` tab on the left
  - Click `Libraries`
  - Click `Install New`
  - Choose `Maven`
  - Paste the following under the `Coordinates`: `org.mongodb.spark:mongo-spark-connector_2.13:10.4.0`

First, let's import our MongoDB credentials information. 

> Note: When you run the notebook on databricks, you might need to re-create the `credentials_mongodb.json` file. This file will only exist in your databricks workspace, but never push it to GitHub.

In [0]:
import json # import json to load credentials
import urllib.parse

# load credentials from json file
with open('credentials_mongodb.json') as f:
    login = json.load(f)

# assign credentials to variables
username = login['username']
password = urllib.parse.quote(login['password'])
host = login['host']
url = "mongodb+srv://{}:{}@{}/?retryWrites=true&w=majority".format(username, password, host)

Let's specify which database and which collection we want to use.

In [0]:
database = "sample_supplies"
collection = "sales"

We can also specify a pre-processing pipeline that we want to pass to MongoDB server before loading the data in Spark. This is usually the recommended way because we want to manipulate MongoDB using its querry, instead of using PySpark querry to wrangle MongoDB data. Only after we have a set of "cleaned" dataset with tabular format, we then import it to Spark.

In [0]:
pipeline = [
    {'$match': {'items.name': 'printer paper'}},
    {'$unwind': {'path': '$items'}},
    {'$addFields': {'totalSale': {'$multiply': ['$items.price', '$items.quantity']}}},
    {'$project': {'saleDate': 1, 'totalSale': 1, '_id': 0}}
]

In [0]:

df = spark.read.format("mongo") \
   .option("uri", url) \
   .option("database", database) \
   .option("collection", collection) \
   .option("pipeline", pipeline)\
   .load()

In [0]:
display(df)

saleDate totalSale 2015-03-23T21:06:49.506Z 80.02 2015-03-23T21:06:49.506Z 70.58 2015-03-23T21:06:49.506Z 280.60 2015-03-23T21:06:49.506Z 155.42 2015-03-23T21:06:49.506Z 36.94 2015-03-23T21:06:49.506Z 159.60 2015-03-23T21:06:49.506Z 24.24 2015-03-23T21:06:49.506Z 42.48 2015-08-25T10:01:02.918Z 80.50 2015-08-25T10:01:02.918Z 254.79 2015-08-25T10:01:02.918Z 62.85 2015-08-25T10:01:02.918Z 3466.00 2015-08-25T10:01:02.918Z 132.36 2015-08-25T10:01:02.918Z 37.55 2015-08-25T10:01:02.918Z 166.56 2015-08-25T10:01:02.918Z 171.60 2015-08-25T10:01:02.918Z 33.36 2017-06-22T09:54:14.185Z 30.08 2017-06-22T09:54:14.185Z 172.76 2017-06-22T09:54:14.185Z 128.40 2017-06-22T09:54:14.185Z 94.23 2017-06-22T09:54:14.185Z 130.68 2017-06-22T09:54:14.185Z 275.80 2017-06-22T09:54:14.185Z 34.28 2017-06-22T09:54:14.185Z 213.20 2017-06-22T09:54:14.185Z 2385.32 2015-02-23T09:53:59.343Z 20.08 2015-02-23T09:53:59.343Z 92.32 2015-02-23T09:53:59.343Z 165.46 2015-02-23T09:53:59.343Z 47.94 2015-02-23T09:53:59.343Z 108.96 2015-02-23T09:53:59.343Z 138.50 2015-02-23T09:53:59.343Z 299.30 2015-02-23T09:53:59.343Z 245.97 2015-02-23T09:53:59.343Z 13.59 2014-11-11T02:13:51.893Z 2416.48 2014-11-11T02:13:51.893Z 77.35 2014-11-11T02:13:51.893Z 104.70 2014-11-11T02:13:51.893Z 305.80 2014-11-11T02:13:51.893Z 89.43 2014-11-11T02:13:51.893Z 155.95 2014-11-11T02:13:51.893Z 47.12 2014-11-11T02:13:51.893Z 73.42 2014-11-11T02:13:51.893Z 207.84 2014-11-11T02:13:51.893Z 14.05 2014-03-31T16:02:06.624Z 175.60 2014-03-31T16:02:06.624Z 27.25 2014-03-31T16:02:06.624Z 33.08 2014-03-31T16:02:06.624Z 174.26 2014-03-31T16:02:06.624Z 106.11 2014-03-31T16:02:06.624Z 170.80 2014-03-31T16:02:06.624Z 237.10 2014-03-31T16:02:06.624Z 2922.80 2014-03-31T16:02:06.624Z 326.97 2014-03-31T16:02:06.624Z 212.20 2015-07-25T07:20:29.804Z 75.21 2015-07-25T07:20:29.804Z 305.55 2015-07-25T07:20:29.804Z 137.60 2015-07-25T07:20:29.804Z 37.41 2015-07-25T07:20:29.804Z 305.41 2014-08-18T10:42:13.935Z 374.32 2014-08-18T10:42:13.935Z 206.10 2014-08-18T10:42:13.935Z 118.75 2014-08-18T10:42:13.935Z 47.20 2017-08-21T20:38:34.618Z 149.60 2017-08-21T20:38:34.618Z 1223.33 2017-08-21T20:38:34.618Z 54.27 2017-08-21T20:38:34.618Z 75.45 2017-08-21T20:38:34.618Z 94.72 2017-08-21T20:38:34.618Z 57.50 2017-08-21T20:38:34.618Z 139.44 2017-08-21T20:38:34.618Z 45.44 2017-12-08T21:40:34.527Z 1613.68 2017-12-08T21:40:34.527Z 74.41 2017-12-08T21:40:34.527Z 383.70 2017-11-12T20:30:15.045Z 29.73 2017-11-12T20:30:15.045Z 88.04 2017-11-12T20:30:15.045Z 114.28 2017-11-12T20:30:15.045Z 153.44 2017-11-12T20:30:15.045Z 181.08 2017-11-12T20:30:15.045Z 4625.28 2017-11-12T20:30:15.045Z 275.16 2015-11-16T22:02:34.415Z 17.30 2015-11-16T22:02:34.415Z 70.08 2015-11-16T22:02:34.415Z 215.30 2015-11-16T22:02:34.415Z 228.08 2015-11-16T22:02:34.415Z 56.16 2015-11-16T22:02:34.415Z 32.20 2015-11-16T22:02:34.415Z 101.00 2015-11-16T22:02:34.415Z 149.48 2015-11-16T22:02:34.415Z 34.61 2015-11-16T22:02:34.415Z 308.10 2015-07-27T20:05:46.464Z 62.91 2015-07-27T20:05:46.464Z 206.64 2015-07-27T20:05:46.464Z 19.32 2015-07-27T20:05:46.464Z 277.75 2015-07-27T20:05:46.464Z 214.71 2015-07-27T20:05:46.464Z 57.58 2015-07-27T20:05:46.464Z 193.44 2015-07-27T20:05:46.464Z 910.07 2015-07-27T20:05:46.464Z 96.78 2015-07-27T20:05:46.464Z 127.30 2013-03-20T16:36:39.112Z 129.15 2013-03-20T16:36:39.112Z 29.20 2013-03-20T16:36:39.112Z 7.49 2013-03-20T16:36:39.112Z 596.36 2013-03-20T16:36:39.112Z 898.84 2013-03-20T16:36:39.112Z 42.02 2013-03-20T16:36:39.112Z 84.24 2013-03-20T16:36:39.112Z 171.84 2013-03-20T16:36:39.112Z 118.14 2013-03-20T16:36:39.112Z 52.28 2015-05-15T13:43:24.561Z 431.55 2015-05-15T13:43:24.561Z 141.08 2015-05-15T13:43:24.561Z 542.81 2015-05-15T13:43:24.561Z 68.80 2015-05-15T13:43:24.561Z 286.95 2015-05-15T13:43:24.561Z 123.93 2015-05-15T13:43:24.561Z 23.48 2015-05-15T13:43:24.561Z 144.76 2017-02-09T12:08:51.353Z 214.20 2015-04-18T03:33:09.638Z 2794.48 2015-04-18T03:33:09.638Z 208.25 2015-04-18T03:33:09.638Z 332.05 2015-04-18T03:33:09.638Z 62.07 2015-04-18T03:33:09.638Z 

Databricks data profile. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

As the first step, let's check how many rows we have and the datatypes

In [0]:
df.count()

2193

In [0]:
df.printSchema()

root
 |-- saleDate: timestamp (nullable = true)
 |-- totalSaleSum: decimal(16,2) (nullable = true)



Let's aggregate the data so we have the total sales per hour

In [0]:
from pyspark.sql.functions import date_trunc
from pyspark.sql import functions as F
df_hourly = (
    df.withColumn("saleDate", date_trunc("hour", df["saleDate"]))
      .orderBy("saleDate")
      .groupBy("saleDate")
      .agg(F.sum("totalSale").alias("totalSaleSum"))
)
display(df_hourly)


saleDate totalSaleSum 2017-12-31T15:00:00Z 838.44 2014-04-01T15:00:00Z 1204.51 2015-05-10T22:00:00Z 7566.56 2017-12-12T09:00:00Z 370.78 2017-02-25T11:00:00Z 4339.57 2016-04-18T23:00:00Z 5330.30 2015-01-30T16:00:00Z 1853.64 2017-04-12T19:00:00Z 3746.59 2017-10-09T21:00:00Z 5378.75 2014-04-06T17:00:00Z 1670.45 2014-08-25T01:00:00Z 5068.37 2015-06-17T04:00:00Z 671.17 2017-09-08T21:00:00Z 4365.73 2017-12-06T15:00:00Z 11993.94 2014-10-01T10:00:00Z 1142.11 2014-06-04T03:00:00Z 494.37 2016-12-31T22:00:00Z 1266.07 2015-07-30T20:00:00Z 608.76 2017-11-18T06:00:00Z 1974.42 2014-09-15T19:00:00Z 3362.93 2013-09-23T02:00:00Z 1153.73 2015-11-07T04:00:00Z 2134.79 2016-01-31T23:00:00Z 8607.19 2013-10-19T18:00:00Z 324.12 2014-07-16T04:00:00Z 542.48 2017-07-31T14:00:00Z 3126.47 2017-06-11T16:00:00Z 595.66 2015-05-10T14:00:00Z 1866.81 2015-08-31T17:00:00Z 319.20 2016-03-22T04:00:00Z 1065.57 2016-09-14T18:00:00Z 1160.37 2016-03-24T19:00:00Z 1360.75 2013-12-06T18:00:00Z 2712.43 2015-02-09T16:00:00Z 1888.60 2014-05-25T00:00:00Z 5716.27 2015-09-28T06:00:00Z 929.81 2013-07-12T17:00:00Z 6082.19 2017-02-21T07:00:00Z 3694.97 2016-05-14T02:00:00Z 332.58 2013-01-18T02:00:00Z 6744.66 2015-11-11T14:00:00Z 1002.03 2015-10-12T06:00:00Z 428.25 2013-04-19T01:00:00Z 547.73 2015-02-22T20:00:00Z 603.11 2016-12-01T12:00:00Z 7555.67 2016-05-21T04:00:00Z 4521.29 2013-05-08T23:00:00Z 1018.49 2017-04-18T22:00:00Z 1167.12 2017-10-13T21:00:00Z 3315.34 2016-02-19T04:00:00Z 1237.44 2014-11-13T21:00:00Z 3950.42 2017-03-14T22:00:00Z 3479.00 2015-07-12T23:00:00Z 2158.44 2013-10-01T19:00:00Z 997.38 2013-02-05T09:00:00Z 6227.79 2014-08-24T05:00:00Z 721.90 2014-07-03T13:00:00Z 624.27 2016-01-30T07:00:00Z 902.81 2017-06-17T05:00:00Z 1328.26 2013-10-03T07:00:00Z 4535.02 2017-01-27T10:00:00Z 3848.20 2017-10-02T06:00:00Z 477.18 2016-08-14T00:00:00Z 4065.86 2014-05-04T01:00:00Z 564.64 2013-04-13T20:00:00Z 1051.54 2013-05-05T17:00:00Z 362.18 2015-02-10T15:00:00Z 2958.75 2013-07-26T22:00:00Z 346.88 2015-09-09T05:00:00Z 1364.11 2014-12-09T03:00:00Z 1705.09 2017-07-11T04:00:00Z 594.37 2013-12-06T07:00:00Z 360.71 2017-08-23T01:00:00Z 7490.98 2013-03-14T06:00:00Z 1152.42 2013-02-04T04:00:00Z 999.91 2016-01-18T00:00:00Z 2531.67 2015-02-19T09:00:00Z 2566.55 2013-06-09T03:00:00Z 1901.95 2017-08-17T06:00:00Z 780.13 2017-12-25T09:00:00Z 83.22 2014-11-11T16:00:00Z 906.29 2014-01-21T10:00:00Z 2350.01 2015-07-12T02:00:00Z 2062.61 2017-09-07T05:00:00Z 5625.37 2017-01-03T04:00:00Z 5802.44 2016-04-23T06:00:00Z 4683.56 2016-08-15T15:00:00Z 874.87 2016-10-07T11:00:00Z 706.17 2013-05-25T18:00:00Z 442.86 2014-12-02T22:00:00Z 3575.28 2014-05-01T20:00:00Z 3671.67 2014-12-31T18:00:00Z 573.33 2015-09-28T04:00:00Z 967.33 2017-07-30T00:00:00Z 7295.93 2013-05-05T21:00:00Z 1223.88 2017-07-20T12:00:00Z 5455.50 2017-05-09T20:00:00Z 1646.41 2013-11-25T23:00:00Z 221.21 2017-03-23T12:00:00Z 1060.56 2015-01-24T18:00:00Z 746.57 2014-02-11T20:00:00Z 3110.48 2014-03-31T17:00:00Z 3856.53 2017-02-07T13:00:00Z 1842.96 2016-10-17T01:00:00Z 6926.66 2014-08-13T02:00:00Z 1954.15 2015-12-23T16:00:00Z 6952.10 2013-06-11T00:00:00Z 1122.04 2017-11-20T10:00:00Z 350.87 2016-08-15T06:00:00Z 4989.11 2014-09-11T07:00:00Z 644.95 2014-06-28T13:00:00Z 99.06 2013-03-12T15:00:00Z 1162.67 2016-12-27T07:00:00Z 6546.74 2017-10-06T18:00:00Z 941.24 2014-06-11T03:00:00Z 5079.46 2017-11-27T03:00:00Z 3170.85 2017-12-03T01:00:00Z 2002.83 2015-09-03T17:00:00Z 659.07 2017-02-11T20:00:00Z 5121.38 2017-10-22T02:00:00Z 264.99 2014-05-01T04:00:00Z 2144.28 2015-10-26T02:00:00Z 4141.47 2015-05-25T06:00:00Z 3249.67 2017-08-19T16:00:00Z 5773.10 2014-06-20T06:00:00Z 854.19 2014-09-28T02:00:00Z 386.80 2016-05-13T06:00:00Z 1325.36 2013-01-21T03:00:00Z 4386.36 2014-04-27T02:00:00Z 3606.78 2013-07-02T23:00:00Z 5472.37 2015-04-17T11:00:00Z 731.05 2014-09-27T17:00:00Z 2699.98 2014-01-26T07:00:00Z 1980.71 2017-12-26T08:00:00Z 541.79 2015-03-23T02:00:00Z 1630.96 2015-07-30T15:00:00Z 86.64 2015-12-09T12:00:00Z 1802.76 2013-07-04T20:00:00Z 775.65 2014-03-28T17:00:00Z 494.

## Removing duplicated values 

You have two options:
- `distinct()` which removes all duplicated values considering the combination of **all** current columns in the DataFrame;
- `drop_duplicates()` which removes all duplicated values considering a specific combination (or set) of columns in the DataFrame;

In [0]:
print(f"Number of rows: {df.count()}")
print(f"Number of unique rows: {df.distinct().count()}")


Number of rows: 15748
Number of unique rows: 15743


In [0]:
df.drop_duplicates().count()

15743

## Join operations



The general syntax for performing join operations in PySpark is as follows:

```python
df_joined = df1.join(
    df2,
    on="common_column",  # or ["common_column1", "common_column2", ...]
    how="join_type"      # join_type can be "inner", "left", "right", "outer", "cross"
)
```

Let's take an example. I want to create a dataframe with every possible hourly timestamps. To do that I will:
- Create a dataframe with all possible hourly timestamp
- Do a left join with the `df_hourly` dataframe

In [0]:
from pyspark.sql.functions import col, sequence, explode

# Generate a complete range of hourly timestamps
min_date = df_hourly.agg(F.min("saleDate")).collect()[0][0]
max_date = df_hourly.agg(F.max("saleDate")).collect()[0][0]

date_range = spark.createDataFrame(
    [(min_date, max_date)], ["start", "end"]
).select(
    sequence(col("start"), col("end"), F.expr("INTERVAL 1 HOUR")).alias("saleDate")
).select(
    explode(col("saleDate")).alias("saleDate")
)

date_range.show(10)

+-------------------+
|           saleDate|
+-------------------+
|2013-01-01 04:00:00|
|2013-01-01 05:00:00|
|2013-01-01 06:00:00|
|2013-01-01 07:00:00|
|2013-01-01 08:00:00|
|2013-01-01 09:00:00|
|2013-01-01 10:00:00|
|2013-01-01 11:00:00|
|2013-01-01 12:00:00|
|2013-01-01 13:00:00|
+-------------------+
only showing top 10 rows



In [0]:
# Join the complete range with the aggregated data 
df_hourly_complete = date_range.join(df_hourly, "saleDate", "left") \
    .select("saleDate", "totalSaleSum") \
    .orderBy("saleDate")

df_hourly_complete.show(10)

+-------------------+------------+
|           saleDate|totalSaleSum|
+-------------------+------------+
|2013-01-01 04:00:00|     4221.97|
|2013-01-01 05:00:00|        NULL|
|2013-01-01 06:00:00|        NULL|
|2013-01-01 07:00:00|        NULL|
|2013-01-01 08:00:00|        NULL|
|2013-01-01 09:00:00|        NULL|
|2013-01-01 10:00:00|        NULL|
|2013-01-01 11:00:00|        NULL|
|2013-01-01 12:00:00|        NULL|
|2013-01-01 13:00:00|        NULL|
+-------------------+------------+
only showing top 10 rows



## Fill in missing values

There will be a lot of missing values because some hours will have no transactions

In [0]:
# count NA values
df_hourly_complete.filter(col("totalSaleSum").isNull()).count()

41619

Let's fill in the missing value using a forward fill approach, which mean we use the last non-NA value to fill the missing values

In [0]:
from pyspark.sql.window import Window
import pyspark.sql.functions as F

# Define a window specification
window_spec = Window.orderBy("saleDate").rowsBetween(Window.unboundedPreceding, Window.currentRow)

# Fill NA values with the nearest non-NA value using forward fill
df_hourly_complete = df_hourly_complete.withColumn(
    "totalSaleSum_filled",
    F.last("totalSaleSum", ignorenulls=True).over(window_spec)
)

display(df_hourly_complete)

saleDate totalSaleSum totalSaleSum_filled 2013-01-01T04:00:00Z 4221.97 4221.97 2013-01-01T05:00:00Z null 4221.97 2013-01-01T06:00:00Z null 4221.97 2013-01-01T07:00:00Z null 4221.97 2013-01-01T08:00:00Z null 4221.97 2013-01-01T09:00:00Z null 4221.97 2013-01-01T10:00:00Z null 4221.97 2013-01-01T11:00:00Z null 4221.97 2013-01-01T12:00:00Z null 4221.97 2013-01-01T13:00:00Z null 4221.97 2013-01-01T14:00:00Z null 4221.97 2013-01-01T15:00:00Z null 4221.97 2013-01-01T16:00:00Z null 4221.97 2013-01-01T17:00:00Z null 4221.97 2013-01-01T18:00:00Z null 4221.97 2013-01-01T19:00:00Z null 4221.97 2013-01-01T20:00:00Z 1425.93 1425.93 2013-01-01T21:00:00Z null 1425.93 2013-01-01T22:00:00Z null 1425.93 2013-01-01T23:00:00Z null 1425.93 2013-01-02T00:00:00Z null 1425.93 2013-01-02T01:00:00Z null 1425.93 2013-01-02T02:00:00Z null 1425.93 2013-01-02T03:00:00Z null 1425.93 2013-01-02T04:00:00Z null 1425.93 2013-01-02T05:00:00Z null 1425.93 2013-01-02T06:00:00Z null 1425.93 2013-01-02T07:00:00Z null 1425.93 2013-01-02T08:00:00Z null 1425.93 2013-01-02T09:00:00Z 3169.27 3169.27 2013-01-02T10:00:00Z null 3169.27 2013-01-02T11:00:00Z null 3169.27 2013-01-02T12:00:00Z null 3169.27 2013-01-02T13:00:00Z null 3169.27 2013-01-02T14:00:00Z null 3169.27 2013-01-02T15:00:00Z null 3169.27 2013-01-02T16:00:00Z null 3169.27 2013-01-02T17:00:00Z null 3169.27 2013-01-02T18:00:00Z null 3169.27 2013-01-02T19:00:00Z null 3169.27 2013-01-02T20:00:00Z 4878.79 4878.79 2013-01-02T21:00:00Z null 4878.79 2013-01-02T22:00:00Z null 4878.79 2013-01-02T23:00:00Z null 4878.79 2013-01-03T00:00:00Z null 4878.79 2013-01-03T01:00:00Z null 4878.79 2013-01-03T02:00:00Z null 4878.79 2013-01-03T03:00:00Z null 4878.79 2013-01-03T04:00:00Z null 4878.79 2013-01-03T05:00:00Z null 4878.79 2013-01-03T06:00:00Z null 4878.79 2013-01-03T07:00:00Z null 4878.79 2013-01-03T08:00:00Z null 4878.79 2013-01-03T09:00:00Z null 4878.79 2013-01-03T10:00:00Z null 4878.79 2013-01-03T11:00:00Z null 4878.79 2013-01-03T12:00:00Z null 4878.79 2013-01-03T13:00:00Z null 4878.79 2013-01-03T14:00:00Z null 4878.79 2013-01-03T15:00:00Z null 4878.79 2013-01-03T16:00:00Z null 4878.79 2013-01-03T17:00:00Z null 4878.79 2013-01-03T18:00:00Z null 4878.79 2013-01-03T19:00:00Z null 4878.79 2013-01-03T20:00:00Z null 4878.79 2013-01-03T21:00:00Z null 4878.79 2013-01-03T22:00:00Z null 4878.79 2013-01-03T23:00:00Z null 4878.79 2013-01-04T00:00:00Z 4700.17 4700.17 2013-01-04T01:00:00Z null 4700.17 2013-01-04T02:00:00Z null 4700.17 2013-01-04T03:00:00Z null 4700.17 2013-01-04T04:00:00Z null 4700.17 2013-01-04T05:00:00Z null 4700.17 2013-01-04T06:00:00Z null 4700.17 2013-01-04T07:00:00Z null 4700.17 2013-01-04T08:00:00Z null 4700.17 2013-01-04T09:00:00Z null 4700.17 2013-01-04T10:00:00Z null 4700.17 2013-01-04T11:00:00Z null 4700.17 2013-01-04T12:00:00Z null 4700.17 2013-01-04T13:00:00Z null 4700.17 2013-01-04T14:00:00Z null 4700.17 2013-01-04T15:00:00Z null 4700.17 2013-01-04T16:00:00Z null 4700.17 2013-01-04T17:00:00Z null 4700.17 2013-01-04T18:00:00Z null 4700.17 2013-01-04T19:00:00Z null 4700.17 2013-01-04T20:00:00Z null 4700.17 2013-01-04T21:00:00Z null 4700.17 2013-01-04T22:00:00Z null 4700.17 2013-01-04T23:00:00Z null 4700.17 2013-01-05T00:00:00Z null 4700.17 2013-01-05T01:00:00Z null 4700.17 2013-01-05T02:00:00Z null 4700.17 2013-01-05T03:00:00Z null 4700.17 2013-01-05T04:00:00Z null 4700.17 2013-01-05T05:00:00Z null 4700.17 2013-01-05T06:00:00Z null 4700.17 2013-01-05T07:00:00Z null 4700.17 2013-01-05T08:00:00Z null 4700.17 2013-01-05T09:00:00Z null 4700.17 2013-01-05T10:00:00Z null 4700.17 2013-01-05T11:00:00Z null 4700.17 2013-01-05T12:00:00Z null 4700.17 2013-01-05T13:00:00Z null 4700.17 2013-01-05T14:00:00Z null 4700.17 2013-01-05T15:00:00Z null 4700.17 2013-01-05T16:00:00Z null 4700.17 2013-01-05T17:00:00Z null 4700.17 2013-01-05T18:00:00Z null 4700.17 2013-01-05T19:00:00Z null 4700.17 2013-01-05T20:00:00Z null 4700.17 2013-01-05T21:00:00Z null 4700.17 2013-01-05T22:00:00Z null 4700.17 2013-01-05T23:00:00Z null 4700.17

You can also decide to drop all NA values

In [0]:
df_hourly_complete.na.drop()\
    .show(10)

+-------------------+------------+-------------------+
|           saleDate|totalSaleSum|totalSaleSum_filled|
+-------------------+------------+-------------------+
|2013-01-01 04:00:00|     4221.97|            4221.97|
|2013-01-01 20:00:00|     1425.93|            1425.93|
|2013-01-02 09:00:00|     3169.27|            3169.27|
|2013-01-02 20:00:00|     4878.79|            4878.79|
|2013-01-04 00:00:00|     4700.17|            4700.17|
|2013-01-06 21:00:00|     1882.69|            1882.69|
|2013-01-07 08:00:00|     5080.12|            5080.12|
|2013-01-07 12:00:00|     5531.05|            5531.05|
|2013-01-08 11:00:00|     5727.18|            5727.18|
|2013-01-08 12:00:00|     1037.97|            1037.97|
+-------------------+------------+-------------------+
only showing top 10 rows



## Pivot operations

Pivot operations in PySpark are used to transform rows into columns, which can be particularly useful for data summarization and analysis. 

#### Columns to rows 

In [0]:
data = [
    ('Agnostic', 27, 34, 60),
    ('Atheist', 12, 27, 37),
    ('Buddhist', 27, 21, 30)
]
cols = ['religion', '<$10k', '$10k-$20k', '$20k-$30k']
religion = spark.createDataFrame(data, cols)
religion.show()

+--------+-----+---------+---------+
|religion|<$10k|$10k-$20k|$20k-$30k|
+--------+-----+---------+---------+
|Agnostic|   27|       34|       60|
| Atheist|   12|       27|       37|
|Buddhist|   27|       21|       30|
+--------+-----+---------+---------+



Stack Expression:

The `stack` function is used to convert multiple columns into rows. The `stack` function takes three arguments:
- The number of columns to be unpivoted (in this case, 3).
- Pairs of column names and their corresponding values.
- The `stack_expr` variable contains the expression to unpivot the columns `<$10k`, `$10k-$20k`, and `$20k-$30k` into two new columns: `salary_range` and `avg_salary`.

In [0]:
from pyspark.sql.functions import expr
stack_expr = """
stack(3,
    '<$10k', `<$10k`,
    '$10k-$20k', `$10k-$20k`,
    '$20k-$30k', `$20k-$30k`
) AS (salary_range, avg_salary)
"""

longer_religion = religion\
    .select('religion', expr(stack_expr))

longer_religion.show()

+--------+------------+----------+
|religion|salary_range|avg_salary|
+--------+------------+----------+
|Agnostic|       <$10k|        27|
|Agnostic|   $10k-$20k|        34|
|Agnostic|   $20k-$30k|        60|
| Atheist|       <$10k|        12|
| Atheist|   $10k-$20k|        27|
| Atheist|   $20k-$30k|        37|
|Buddhist|       <$10k|        27|
|Buddhist|   $10k-$20k|        21|
|Buddhist|   $20k-$30k|        30|
+--------+------------+----------+



#### Rows to columns

In [0]:
from pyspark.sql.functions import first
# Equivalent to the `religion` DataFrame:
longer_religion\
    .groupby('religion')\
    .pivot('salary_range')\
    .agg(first('avg_salary'))\
    .show()

+--------+---------+---------+-----+
|religion|$10k-$20k|$20k-$30k|<$10k|
+--------+---------+---------+-----+
|Agnostic|       34|       60|   27|
|Buddhist|       21|       30|   27|
| Atheist|       27|       37|   12|
+--------+---------+---------+-----+



### Collecting and Expanding Operations

In PySpark, collecting and expanding operations are useful for transforming and manipulating data, especially when dealing with nested structures or arrays.

#### Exploding
The `explode` function is used to transform an array or map column into multiple rows. This is particularly useful when you have nested data and want to flatten it.

In [0]:
data = [
    (1, ["R", "Python"], {'dep': 'PR', 'name': 'Anne'}),
    (2, ["Scala"], {'dep': 'PM', 'name': 'Mike'}),
    (3, ["Java", "Python"], {'dep': 'HF', 'name': 'Sam'})
]
columns = ["employee_id", "knowledge", "employee_attrs"]
employees = spark.createDataFrame(data, columns)
employees.show()

+-----------+--------------+--------------------+
|employee_id|     knowledge|      employee_attrs|
+-----------+--------------+--------------------+
|          1|   [R, Python]|{name -> Anne, de...|
|          2|       [Scala]|{name -> Mike, de...|
|          3|[Java, Python]|{name -> Sam, dep...|
+-----------+--------------+--------------------+



When you apply the `explode()` function over a column of arrays, this function will create a new row for each element in each array it finds in the column

In [0]:
from pyspark.sql.functions import explode
explode_array = employees\
    .select(
        'employee_id',
        explode('knowledge')
    )

explode_array.show()

+-----------+------+
|employee_id|   col|
+-----------+------+
|          1|     R|
|          1|Python|
|          2| Scala|
|          3|  Java|
|          3|Python|
+-----------+------+



On the other hand, instead of arrays, the behaviour of` explode()` is slightly different when you apply it over a column of maps. Because each element in a map have two components: a key and a value. 

As a consequence, when you apply `explode()` over a column of maps, each element in the map generates two different rows, which are stored in two separated columns, called key and value.

In [0]:
explode_map = employees\
    .select(
        'employee_id',
        explode('employee_attrs')
    )

explode_map.show()

+-----------+----+-----+
|employee_id| key|value|
+-----------+----+-----+
|          1|name| Anne|
|          1| dep|   PR|
|          2|name| Mike|
|          2| dep|   PM|
|          3|name|  Sam|
|          3| dep|   HF|
+-----------+----+-----+



This kind of output is powerful, specially with pivot operations, because you can easily organize all the data found in a column of maps into a series of new columns, like this:

In [0]:
explode_map\
    .groupby('employee_id')\
    .pivot('key')\
    .agg(first('value'))\
    .show()

+-----------+---+----+
|employee_id|dep|name|
+-----------+---+----+
|          1| PR|Anne|
|          2| PM|Mike|
|          3| HF| Sam|
+-----------+---+----+




#### Collecting
The `collect` method is used to retrieve the entire DataFrame as a list of Row objects. This is typically used for small datasets due to memory constraints.

In [0]:
data = [
    (1, "Python"),
    (1, "SQL"),
    (2, "Java"),
    (2, "Scala"),
    (3, "Python"),
    (3, "Python"),
    (4, "Scala"),
    (4, "SQL")
]
explode_array = spark.createDataFrame(data, ["employee_id", "col"])
display(explode_array)

employee_id col 1 Python 1 SQL 2 Java 2 Scala 3 Python 3 Python 4 Scala 4 SQL

In reverse, you can use the `collect_list()` and `collect_set()` functions to retract your DataFrame. That is, to reduce the number of rows of the DataFrame, while keeping the same amount of information.

The `collect_list` function collects all values in a column into an array, **including duplicates.**

In [0]:
from pyspark.sql.functions import collect_list

# Collecting all 'col' values into a list for each 'employee_id'
knowledge_list = explode_array.groupBy("employee_id").agg(collect_list("col").alias("knowledge_list"))
display(knowledge_list)

employee_id knowledge_list 1 List(Python, SQL) 2 List(Java, Scala) 3 List(Python, Python) 4 List(Scala, SQL)

The `collect_set` function collects all unique values in a column into an array, **removing duplicates.**

In [0]:
from pyspark.sql.functions import collect_set

# Collecting unique 'col' values into a set for each 'employee_id'
knowledge_set = explode_array.groupBy("employee_id").agg(collect_set("col").alias("knowledge_set"))
display(knowledge_set)

employee_id knowledge_set 1 List(Python, SQL) 2 List(Scala, Java) 3 List(Python) 4 List(Scala, SQL)